In [1]:
import tweepy
from twitter_authentication import bearer_token
import time
import pandas as pd
import json 
import pickle
import folium
from folium.plugins import MarkerCluster
import json
import csv
from pathlib import Path
import glob, os, json


In [3]:
def json_load(filepath):
    with open(filepath, "r") as json_file:
        data = json.load(json_file)
    return data

def json_dump(data, filepath, pretty_format = True):
    with open(filepath, 'w') as fw:
        if pretty_format:
            json.dump(data, fw, indent=2, sort_keys=True)
        else:
            json.dump(data, fw)

def pickle_dump(obj, pickle_filepath):
    with open(pickle_filepath, "wb") as f:
        pickle.dump(obj, f, protocol=2)

def pickle_load(pickle_filepath):
    with open(pickle_filepath, "rb") as f:
        obj = pickle.load(f)
    return obj

In [4]:
client = tweepy.Client(bearer_token, wait_on_rate_limit=True)

In [25]:
def get_tweets(place_dict = {},
               user_dict = {},
               tweet_dict = {},
                next_token = None,
               alz_tweets = [], 
                query = 'alzheimers disease -is:retweet place_country:US',
              user_fields = ['username', 'public_metrics', 'description', 'location'],
              place_fields = ['place_type', 'geo'],
              tweet_fields = ['created_at', 'geo', 'public_metrics', 'text'],
              expansions = ['author_id', 'geo.place_id'],
              start_time = '2010-01-01T00:00:00Z',
               end_time = '2023-01-15T00:00:00Z'
              ):
    place_keys= ["full_name", 'id', 'contained_within', 'country', 'country_code', 'geo', 'name', 'place_type' ]
    user_keys= ['id', 'name', 'username', 'created_at', 
            'description', "entities", 'location', 'pinned_tweet_id', 
            'profile_image_url', 'protected', 'public_metrics', 'url', 'verified', 'withheld']
    tweet_keys = ['id', 'text', 'author_id', 'context_annotations',
             'conversation_id', 'entities', 'in_reply_to_user_id', 'lang',
             'non_public_metrics', 'organic_metrics', 'possibly_sensitive',
             'promoted_metrics', 'public_metrics', 'referenced_tweets', 'reply_settings',
             'source', 'withheld']    


    for tweet in tweepy.Paginator(client.search_all_tweets, 
                                     query = query,
                                     user_fields = user_fields,
                                     place_fields = place_fields,
                                     tweet_fields = tweet_fields,
                                     expansions = expansions,
                                     start_time = start_time,
                                     end_time = end_time,
                                  pagination_token = next_token,
                                  max_results=500):
        time.sleep(1)
        alz_tweets.append(tweet)
    
    
    # Loop through each response object
    for response in alz_tweets:
        # Take all of the users, and put them into a dictionary of dictionaries with the info we want to keep
        for place in response.includes['places']:
            place_obj = {}
            for key in place_keys:
                place_obj[key] = place[key]
            place_dict[place_obj['id']] = place_obj
        for user in response.includes['users']:
            user_obj = {}
            for key in user_keys:
                user_obj[key] = user[key]
            user_dict[user_obj['id']] = user_obj

        for tweet in response.data:
            tweet_obj = {}
            for key in tweet_keys:
                tweet_obj[key] = getattr(tweet, key)
            tweet_dict[tweet_obj['id']] = tweet_obj
    
    return place_dict, user_dict, tweet_dict, next_token, alz_tweets



In [26]:
next_token = None
place_dict = {}
user_dict = {}
tweet_dict = {}
alz_tweets = []



place_dict, user_dict, tweet_dict, next_token, alz_tweets = get_tweets(place_dict,user_dict,tweet_dict, next_token, alz_tweets)

In [27]:
response = alz_tweets[0]

In [111]:
# print(len(response.data))
# for tweet in response.data:
#     print(dict(tweet))

In [34]:
tweets_data = []
for tweet in response.data:
    #print(dict(tweet))
    for place in response.includes['places']:
        if tweet.geo is not None:
            if tweet.geo['place_id'] == place['id']:
                tweet_info = {
                    "id": tweet.id,
                    "content": tweet.text,
                    "geo_id": place['id'] if place is not None else None,
                    "geo_info": dict(place)
                }
                tweets_data.append(tweet_info)

In [35]:
print(tweets_data[0])

{'id': 1613926491200552961, 'content': 'Neuroscientists reveal how a toxic form of tau protein, #taupT217, spreads through the brain as #Alzheimers disease progresses\n\nhttps://t.co/LkvPgdlntB', 'geo_id': 'ab2f2fac83aa388d', 'geo_info': {'full_name': 'Oakland, CA', 'geo': {'type': 'Feature', 'bbox': [-122.34266, 37.699279, -122.114711, 37.8847092], 'properties': {}}, 'id': 'ab2f2fac83aa388d', 'place_type': 'city'}}


In [37]:
print(len(tweets_data))

475


In [110]:
# for tweet in tweets_data:
#     print(tweet)
#     print()

In [38]:
json_dump(tweets_data, filepath = "Full_List/alzheimers_disease.json")

In [7]:
def get_tweets2(place_dict = {},
               user_dict = {},
               tweet_dict = {},
                next_token = None,
               alz_tweets = [],
                query = 'alzheimer\'s disease -is:retweet place_country:US',
              user_fields = ['username', 'public_metrics', 'description', 'location'],
              place_fields = ['place_type', 'geo'],
              tweet_fields = ['created_at', 'geo', 'public_metrics', 'text'],
              expansions = ['author_id', 'geo.place_id'],
              start_time = '2010-01-01T00:00:00Z',
               end_time = '2023-01-15T00:00:00Z'
              ):
    place_keys= ["full_name", 'id', 'contained_within', 'country', 'country_code', 'geo', 'name', 'place_type' ]
    user_keys= ['id', 'name', 'username', 'created_at', 
            'description', "entities", 'location', 'pinned_tweet_id', 
            'profile_image_url', 'protected', 'public_metrics', 'url', 'verified', 'withheld']
    tweet_keys = ['id', 'text', 'author_id', 'context_annotations',
             'conversation_id', 'entities', 'in_reply_to_user_id', 'lang',
             'non_public_metrics', 'organic_metrics', 'possibly_sensitive',
             'promoted_metrics', 'public_metrics', 'referenced_tweets', 'reply_settings',
             'source', 'withheld']    


    for tweet in tweepy.Paginator(client.search_all_tweets, 
                                     query = query,
                                     user_fields = user_fields,
                                     place_fields = place_fields,
                                     tweet_fields = tweet_fields,
                                     expansions = expansions,
                                     start_time = start_time,
                                     end_time = end_time,
                                  pagination_token = next_token,
                                  max_results=500):
        time.sleep(1)
        alz_tweets.append(tweet)
    
    
    return alz_tweets



In [8]:
next_token = None
place_dict = {}
user_dict = {}
tweet_dict = {}
alz_tweets = []



alz_tweets = get_tweets2(place_dict,user_dict,tweet_dict, next_token, alz_tweets)

In [42]:
response = alz_tweets[0]

In [43]:
tweets_data = []
for tweet in response.data:
    #print(dict(tweet))
    for place in response.includes['places']:
        if tweet.geo is not None:
            if tweet.geo['place_id'] == place['id']:
                tweet_info = {
                    "id": tweet.id,
                    "content": tweet.text,
                    "geo_id": place['id'] if place is not None else None,
                    "geo_info": dict(place)
                }
                tweets_data.append(tweet_info)
                #print(dict(place))

In [44]:
print(len(tweets_data))

421


In [45]:
json_dump(tweets_data, filepath = "Full_List/alzheimer\'s_disease.json")

In [9]:
def get_tweets3(place_dict = {},
               user_dict = {},
               tweet_dict = {},
                next_token = None,
               alz_tweets = [],
                query = 'alzheimer -is:retweet place_country:US',
              user_fields = ['username', 'public_metrics', 'description', 'location'],
              place_fields = ['place_type', 'geo'],
              tweet_fields = ['created_at', 'geo', 'public_metrics', 'text'],
              expansions = ['author_id', 'geo.place_id'],
              start_time = '2010-01-01T00:00:00Z',
               end_time = '2023-01-15T00:00:00Z'
              ):
    place_keys= ["full_name", 'id', 'contained_within', 'country', 'country_code', 'geo', 'name', 'place_type' ]
    user_keys= ['id', 'name', 'username', 'created_at', 
            'description', "entities", 'location', 'pinned_tweet_id', 
            'profile_image_url', 'protected', 'public_metrics', 'url', 'verified', 'withheld']
    tweet_keys = ['id', 'text', 'author_id', 'context_annotations',
             'conversation_id', 'entities', 'in_reply_to_user_id', 'lang',
             'non_public_metrics', 'organic_metrics', 'possibly_sensitive',
             'promoted_metrics', 'public_metrics', 'referenced_tweets', 'reply_settings',
             'source', 'withheld']    


    for tweet in tweepy.Paginator(client.search_all_tweets, 
                                     query = query,
                                     user_fields = user_fields,
                                     place_fields = place_fields,
                                     tweet_fields = tweet_fields,
                                     expansions = expansions,
                                     start_time = start_time,
                                     end_time = end_time,
                                  pagination_token = next_token,
                                  max_results=500):
        time.sleep(1)
        alz_tweets.append(tweet)
    
    
    return alz_tweets



In [10]:
next_token = None
place_dict = {}
user_dict = {}
tweet_dict = {}
alz_tweets = []



alz_tweets = get_tweets3(place_dict,user_dict,tweet_dict, next_token, alz_tweets)

Rate limit exceeded. Sleeping for 70 seconds.


In [11]:
response = alz_tweets[0]

In [14]:
tweets_data = []
for tweet in response.data:
    for place in response.includes['places']:
        if tweet.geo is not None:
            if tweet.geo['place_id'] == place['id']:
                tweet_info = {
                    "id": tweet.id,
                    "content": tweet.text,
                    "geo_id": place['id'] if place is not None else None,
                    "geo_info": dict(place)
                }
                tweets_data.append(tweet_info)

In [17]:
print(len(tweets_data))

408


In [16]:
json_dump(tweets_data, filepath = "Full_List/alzheimer.json")

In [18]:
def get_tweets4(place_dict = {},
               user_dict = {},
               tweet_dict = {},
                next_token = None,
               alz_tweets = [],
                query = 'alzheimers -is:retweet place_country:US',
              user_fields = ['username', 'public_metrics', 'description', 'location'],
              place_fields = ['place_type', 'geo'],
              tweet_fields = ['created_at', 'geo', 'public_metrics', 'text'],
              expansions = ['author_id', 'geo.place_id'],
              start_time = '2010-01-01T00:00:00Z',
               end_time = '2023-01-15T00:00:00Z'
              ):
    place_keys= ["full_name", 'id', 'contained_within', 'country', 'country_code', 'geo', 'name', 'place_type' ]
    user_keys= ['id', 'name', 'username', 'created_at', 
            'description', "entities", 'location', 'pinned_tweet_id', 
            'profile_image_url', 'protected', 'public_metrics', 'url', 'verified', 'withheld']
    tweet_keys = ['id', 'text', 'author_id', 'context_annotations',
             'conversation_id', 'entities', 'in_reply_to_user_id', 'lang',
             'non_public_metrics', 'organic_metrics', 'possibly_sensitive',
             'promoted_metrics', 'public_metrics', 'referenced_tweets', 'reply_settings',
             'source', 'withheld']    


    for tweet in tweepy.Paginator(client.search_all_tweets, 
                                     query = query,
                                     user_fields = user_fields,
                                     place_fields = place_fields,
                                     tweet_fields = tweet_fields,
                                     expansions = expansions,
                                     start_time = start_time,
                                     end_time = end_time,
                                  pagination_token = next_token,
                                  max_results=500):
        time.sleep(1)
        alz_tweets.append(tweet)
    
    
    return alz_tweets



In [19]:
next_token = None
place_dict = {}
user_dict = {}
tweet_dict = {}
alz_tweets = []



alz_tweets = get_tweets4(place_dict,user_dict,tweet_dict, next_token, alz_tweets)

Rate limit exceeded. Sleeping for 23 seconds.


In [20]:
response = alz_tweets[0]

In [22]:
tweets_data = []
for tweet in response.data:
    #print(dict(tweet))
    for place in response.includes['places']:
        if tweet.geo is not None:
            if tweet.geo['place_id'] == place['id']:
                tweet_info = {
                    "id": tweet.id,
                    "content": tweet.text,
                    "geo_id": place['id'] if place is not None else None,
                    "geo_info": dict(place)
                }
                tweets_data.append(tweet_info)
                #print(dict(place))

In [23]:
print(len(tweets_data))

466


In [24]:
json_dump(tweets_data, filepath = "Full_List/alzheimers.json")

In [25]:
def get_tweets6(place_dict = {},
               user_dict = {},
               tweet_dict = {},
                next_token = None,
               alz_tweets = [],
                query = 'dementia -is:retweet place_country:US',
              user_fields = ['username', 'public_metrics', 'description', 'location'],
              place_fields = ['place_type', 'geo'],
              tweet_fields = ['created_at', 'geo', 'public_metrics', 'text'],
              expansions = ['author_id', 'geo.place_id'],
              start_time = '2010-01-01T00:00:00Z',
               end_time = '2023-01-15T00:00:00Z'
              ):
    place_keys= ["full_name", 'id', 'contained_within', 'country', 'country_code', 'geo', 'name', 'place_type' ]
    user_keys= ['id', 'name', 'username', 'created_at', 
            'description', "entities", 'location', 'pinned_tweet_id', 
            'profile_image_url', 'protected', 'public_metrics', 'url', 'verified', 'withheld']
    tweet_keys = ['id', 'text', 'author_id', 'context_annotations',
             'conversation_id', 'entities', 'in_reply_to_user_id', 'lang',
             'non_public_metrics', 'organic_metrics', 'possibly_sensitive',
             'promoted_metrics', 'public_metrics', 'referenced_tweets', 'reply_settings',
             'source', 'withheld']    


    for tweet in tweepy.Paginator(client.search_all_tweets, 
                                     query = query,
                                     user_fields = user_fields,
                                     place_fields = place_fields,
                                     tweet_fields = tweet_fields,
                                     expansions = expansions,
                                     start_time = start_time,
                                     end_time = end_time,
                                  pagination_token = next_token,
                                  max_results=500):
        time.sleep(1)
        alz_tweets.append(tweet)
    
    
    return alz_tweets



In [26]:
next_token = None
place_dict = {}
user_dict = {}
tweet_dict = {}
alz_tweets = []



alz_tweets = get_tweets6(place_dict,user_dict,tweet_dict, next_token, alz_tweets)

Rate limit exceeded. Sleeping for 16 seconds.


In [27]:
response = alz_tweets[0]

In [29]:
tweets_data = []
for tweet in response.data:
    #print(dict(tweet))
    for place in response.includes['places']:
        if tweet.geo is not None:
            if tweet.geo['place_id'] == place['id']:
                tweet_info = {
                    "id": tweet.id,
                    "content": tweet.text,
                    "geo_id": place['id'] if place is not None else None,
                    "geo_info": dict(place)
                }
                tweets_data.append(tweet_info)
                #print(dict(place))

In [30]:
print(len(tweets_data))

491


In [31]:
json_dump(tweets_data, filepath = "Full_List/dementia.json")

In [32]:
def get_tweets5(place_dict = {},
               user_dict = {},
               tweet_dict = {},
                next_token = None,
               alz_tweets = [],
                query = 'cognitive decline -is:retweet place_country:US',
              user_fields = ['username', 'public_metrics', 'description', 'location'],
              place_fields = ['place_type', 'geo'],
              tweet_fields = ['created_at', 'geo', 'public_metrics', 'text'],
              expansions = ['author_id', 'geo.place_id'],
              start_time = '2010-01-01T00:00:00Z',
               end_time = '2023-01-15T00:00:00Z'
              ):
    place_keys= ["full_name", 'id', 'contained_within', 'country', 'country_code', 'geo', 'name', 'place_type' ]
    user_keys= ['id', 'name', 'username', 'created_at', 
            'description', "entities", 'location', 'pinned_tweet_id', 
            'profile_image_url', 'protected', 'public_metrics', 'url', 'verified', 'withheld']
    tweet_keys = ['id', 'text', 'author_id', 'context_annotations',
             'conversation_id', 'entities', 'in_reply_to_user_id', 'lang',
             'non_public_metrics', 'organic_metrics', 'possibly_sensitive',
             'promoted_metrics', 'public_metrics', 'referenced_tweets', 'reply_settings',
             'source', 'withheld']    


    for tweet in tweepy.Paginator(client.search_all_tweets, 
                                     query = query,
                                     user_fields = user_fields,
                                     place_fields = place_fields,
                                     tweet_fields = tweet_fields,
                                     expansions = expansions,
                                     start_time = start_time,
                                     end_time = end_time,
                                  pagination_token = next_token,
                                  max_results=500):
        time.sleep(1)
        alz_tweets.append(tweet)
    
    
    return alz_tweets



In [33]:
next_token = None
place_dict = {}
user_dict = {}
tweet_dict = {}
alz_tweets = []



alz_tweets = get_tweets5(place_dict,user_dict,tweet_dict, next_token, alz_tweets)

In [34]:
response = alz_tweets[0]

In [35]:
tweets_data = []
for tweet in response.data:
    #print(dict(tweet))
    for place in response.includes['places']:
        if tweet.geo is not None:
            if tweet.geo['place_id'] == place['id']:
                tweet_info = {
                    "id": tweet.id,
                    "content": tweet.text,
                    "geo_id": place['id'] if place is not None else None,
                    "geo_info": dict(place)
                }
                tweets_data.append(tweet_info)
                #print(dict(place))

In [36]:
print(len(tweets_data))

474


In [37]:
json_dump(tweets_data, filepath = "Full_List/cognitive_decline.json")

In [39]:
import os
import json

folder_path = "Full_List"
merged_data = {}

# Iterate through all JSON files in the folder
for filename in os.listdir(folder_path):
    if filename.endswith(".json"):
        file_path = os.path.join(folder_path, filename)
        
        # Read the JSON file and merge its content into the merged_data dictionary
        with open(file_path, 'r') as file:
            data = json.load(file)
        
        if isinstance(data, list):
            data_dict = {tweet['id']: tweet for tweet in data}
            merged_data.update(data_dict)
        elif isinstance(data, dict):
            merged_data.update(data)

# Print the first item in the merged_data dictionary
#print(merged_dat)

In [40]:
df = pd.DataFrame.from_dict(merged_data)

In [41]:
new_transposed = df.transpose()
new_transposed

content  \
1614321118785175552  The drug, lecanemab, was proven to moderately ...   
1613987178157072384  @TommyKakari highlighting the complimentary na...   
1613951789325324302  Health has the chance to make new, life-saving...   
1613926491200552961  Neuroscientists reveal how a toxic form of tau...   
1613754692307390471  Grateful for Dr. Anderson and the opportunity ...   
...                                                                ...   
1604325279454871555  @ninaturner He's YOUR guy!!  I didn't vote for...   
1604296980007616513  @Julius_Kim Fifty?\nYou're still a baby. Happy...   
1604293580868419584  Omg. This was a president thanks to Putin. How...   
1604290311127121920  Until Alzheimer’s joins the conversation 😪 htt...   
1604241286420385792  @NicoleArbour Could argue good for Alzheimer’s...   

                               geo_id  \
1614321118785175552  3df4f427b5a60fea   
1613987178157072384  04cb31bae3b3af93   
1613951789325324302  014f4cd64f60daea   
1613926491200552961  ab2f2fac83aa388d   
1613754692307390471  d374fb61a20fb74f   
...                               ...   
1604325279454871555  dce44ec49eb788f5   
1604296980007616513  1c69a67ad480e1b1   
1604293580868419584  7b72e3a619e4e202   
1604290311127121920  97290292acb29ff8   
1604241286420385792  1935ab8020a2553b   

                                                              geo_info  \
1614321118785175552  {'full_name': 'San Antonio, TX', 'geo': {'bbox...   
1613987178157072384  {'full_name': 'Miami, FL', 'geo': {'bbox': [-8...   
1613951789325324302  {'full_name': 'Cockeysville, MD', 'geo': {'bbo...   
1613926491200552961  {'full_name': 'Oakland, CA', 'geo': {'bbox': [...   
1613754692307390471  {'full_name': 'Nevada, USA', 'geo': {'bbox': [...   
...                                                                ...   
1604325279454871555  {'full_name': 'Irving, TX', 'geo': {'bbox': [-...   
1604296980007616513  {'full_name': 'Houston, TX', 'geo': {'bbox': [...   
1604293580868419584  {'full_name': 'Redlands, CO', 'geo': {'bbox': ...   
1604290311127121920  {'full_name': 'Signal Hill, CA', 'geo': {'bbox...   
1604241286420385792  {'full_name': 'Millburn, NJ', 'geo': {'bbox': ...   

                                      id  
1614321118785175552  1614321118785175552  
1613987178157072384  1613987178157072384  
1613951789325324302  1613951789325324302  
1613926491200552961  1613926491200552961  
1613754692307390471  1613754692307390471  
...                                  ...  
1604325279454871555  1604325279454871555  
1604296980007616513  1604296980007616513  
1604293580868419584  1604293580868419584  
1604290311127121920  1604290311127121920  
1604241286420385792  1604241286420385792  

[2415 rows x 4 columns]

In [49]:
long = []
lat = []
full_name = []

for location in new_transposed.geo_info:
    #print(location)
    long.append(location['geo']['bbox'][0])
    lat.append(location['geo']['bbox'][1])
    full_name.append(location['full_name'])

In [50]:
df = pd.DataFrame({'Name':full_name, 'Long':long,'Lat':lat})

In [51]:
df

Name        Long        Lat
0      San Antonio, TX  -98.778559  29.141956
1            Miami, FL  -80.321683  25.709040
2     Cockeysville, MD  -76.672912  39.453647
3          Oakland, CA -122.342660  37.699279
4          Nevada, USA -120.005740  35.002086
...                ...         ...        ...
2410        Irving, TX  -97.034184  32.771786
2411       Houston, TX  -95.823268  29.522325
2412      Redlands, CO -108.703851  39.036603
2413   Signal Hill, CA -118.184987  33.789789
2414      Millburn, NJ  -74.372452  40.713302

[2415 rows x 3 columns]

In [52]:
map = folium.Map(location=[df.Lat.mean(), df.Long.mean()], zoom_start=4.3, control_scale=True)
cluster = MarkerCluster(name="Tweet Density").add_to(map)


In [54]:
for index, location_info in df.iterrows():
    folium.Circle(
        location=[location_info["Lat"], location_info["Long"]], 
        popup=location_info["Name"],
        radius=100000,
        #color='crimson',
        #fill=True,
        #fill_color='crimson'
    ).add_to(cluster)

In [55]:
map

In [1]:
# Saving all tweets in separate file 

import os
import json

# Initialize an empty list to store the tweet content
tweet_content_list = []

# Set the directory path
dir_path = "Full_List"

# Loop through all the files in the directory
for filename in os.listdir(dir_path):
    # Check if the file is a JSON file
    if filename.endswith(".json"):
        # Create the full file path by joining the directory path and the filename
        file_path = os.path.join(dir_path, filename)
        
        # Open the JSON file and load its content
        with open(file_path, "r") as f:
            data = json.load(f)
        
        # Loop through the list of tweets in the JSON file
        for tweet in data:
            # Extract the tweet content and append it to the tweet_content_list
            content = tweet.get("content")
            if content:
                tweet_content_list.append(content)

# Create the output directory if it doesn't exist
output_dir = "Recollected_tweets"
os.makedirs(output_dir, exist_ok=True)

# Define the output file path
output_file_path = os.path.join(output_dir, "all_tweet_contents.json")

# Save the tweet_content_list to the output JSON file
with open(output_file_path, "w") as f:
    json.dump(tweet_content_list, f, ensure_ascii=False, indent=4)

print(f"Saved all tweet contents to {output_file_path}")

Saved all tweet contents to Recollected_tweets/all_tweet_contents.json


In [2]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

In [3]:
# Example labeled dataset (raw tweets and their corresponding categories)
raw_data = [
    ("I've been diagnosed with diabetes and it's been really tough to manage.", "patients"),
    ("My mom has Alzheimer's and I'm taking care of her.", "caregivers"),
    ("Just heard about the new COVID-19 vaccine, hope it's effective!", "general population"),
    ("Taking my dad to his doctor's appointment today.", "caregivers"),
    ("I love playing basketball on weekends!", "unrelated"),
    ("Living with a chronic illness can be challenging, but I'm trying my best to cope.", "patients"),
    ("Any advice for managing anxiety in public?", "general population"),
    ("Just got the flu shot, trying to stay healthy this winter.", "general population"),
    ("My wife was diagnosed with breast cancer, and we're seeking support groups.", "caregivers"),
    ("Going out for a walk with my dog.", "unrelated")
]

# Separate raw tweets and categories
raw_tweets, categories = zip(*raw_data)

# Preprocess the raw tweets (e.g., lowercasing, tokenization, stopword removal, etc.)
def preprocess_text(text):
    # Add your text preprocessing logic here
    return text.lower()

tweets = [preprocess_text(raw_tweet) for raw_tweet in raw_tweets]

In [5]:
# Extract features using TF-IDF
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(tweets)
y = categories

In [6]:
# Split the data into a training set and a test set
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [11]:
# Train a Logistic Regression model
model = LogisticRegression()
model.fit(X_train, y_train)

LogisticRegression()

In [14]:
# Evaluate the model on the test set
y_pred = model.predict(X_test)
print(classification_report(y_test, y_pred, zero_division=0))

                    precision    recall  f1-score   support

        caregivers       0.00      0.00      0.00       2.0
general population       0.00      0.00      0.00       0.0

          accuracy                           0.00       2.0
         macro avg       0.00      0.00      0.00       2.0
      weighted avg       0.00      0.00      0.00       2.0



In [16]:
# Load the new tweets from the JSON file
with open("Recollected_tweets/all_tweet_contents.json", "r") as f:
    raw_new_tweets = json.load(f)

# Preprocess the new tweets
new_tweets = [preprocess_text(raw_tweet) for raw_tweet in raw_new_tweets]

# Extract features for the new tweets using the same vectorizer used for the training data
new_tweet_features = vectorizer.transform(new_tweets)

# Classify the new tweets using the trained model
predicted_categories = model.predict(new_tweet_features)

# Print the results
for tweet, category in zip(raw_new_tweets, predicted_categories):
    print(f"Tweet: {tweet}\nCategory: {category}\n")

Tweet: The drug, lecanemab, was proven to moderately slow early stage Alzheimer’s. It also comes with the potential for some serious side effects, such as brain bleeding and brain inflammation. @Joshua_Peck_ https://t.co/k2VcUlYzZd
Category: general population

Tweet: @TommyKakari highlighting the complimentary nature of biofluids and neuroimaging in #Alzheimers biomarker studies ... Quite the perspective he offers @HAIconference 👏👏👏

I wonder if the third side of the coin might be #neuropathology 😉🔬🧠 https://t.co/bU4Dbf6Ltf
Category: general population

Tweet: Health has the chance to make new, life-saving gene therapy treatments available to people for the first time ever. But Big Pharma’s millions-of-dollars-a-dose price tags present major problems. https://t.co/xxvJqCu0PU
Category: general population

Tweet: Neuroscientists reveal how a toxic form of tau protein, #taupT217, spreads through the brain as #Alzheimers disease progresses

https://t.co/LkvPgdlntB
Category: general popula